In [ ]:
import gradio as gr
from transformers.utils import logging
import time
import joblib
import re
import numpy as np

from src import get_lexical_desc,get_morphemic_desc, preprocess

logging.set_verbosity_info()
logger = logging.get_logger("transformers")

In [ ]:
loaded_rf = joblib.load("rfc_30_0.95.joblib")
folders = ['eastern', 'western', 'grabar']

text='western - Աստուած ըսաւ. «Մեր պատկերով, մեր նմանութեան պէս մարդ ընենք, որ տիրապետէն ծովու ձուկերուն, երկինքի թռչուններուն եւ ընտանի անասուններուն, ամբողջ երկրին, ու երկրի վրայ ըսողացող բոլոր սողուններուն».* 27 Աստուած իր պատկերով ստեղծեց մարդը'


words=preprocess(text)
print(len(words))
desc_lexical=get_lexical_desc(words).reshape((1,-1))
desc_morphemic=get_morphemic_desc(words).reshape((1,-1))


data=np.concatenate([desc_morphemic,desc_lexical],axis=1)

loaded_rf.predict_proba(data)[0]

In [ ]:
def classify(input_text_message: str):

    logger.info(time.strftime("%Y.%m.%d, %H:%M:%S")+' '+'input text message: '+input_text_message)

    words=preprocess(input_text_message)
    desc_lexical=get_lexical_desc(words).reshape((1,-1))
    desc_morphemic=get_morphemic_desc(words).reshape((1,-1))
    
    data=np.concatenate([desc_morphemic,desc_lexical],axis=1)
    prediction=loaded_rf.predict_proba(data)[0]

    confidences = {labels[i]: float(prediction[i]) for i in range(3)}

    logger.info(time.strftime("%Y.%m.%d, %H:%M:%S")+' '+'result '+str(confidences))
    
    return confidences, len(words)

labels = ['eastern armenian', 'western armenian', 'grabar (classic) armenian']

loaded_rf = joblib.load("rfc_30_0.95.joblib")

examples=['western bible  -  Զաւակնե՜ր, վերջին ժամն է. եւ ինչպէս լսեցիք թէ ՛՛Նեռը պիտի գայ, արդէ՜ն ջատ նեռեր կան. ատկէ կը գիտնանք թէ վերջին ժամն է։ 19 Անոնք մեր մէջէն ելան, բայց մեզմէ չէին, որովհետեւ եթէ ըլլային մեզմէ, կը մնային մեզի հետ։ Բայց մեզմէ ելան, որպէսզի բացայայտուի թէ անոնք բոլորն ալ մեզմէ չէին։ 20 Սակայն դուք օծութիւն ունիք Սուրբէն, ու գիտէք ամէն բան։',
          
'grabar bible - 1 Եւ տեսեալ զժողովուրդսն ել ի լեառն. եւ իբրեւ նստաւ անդ մատեան առ նա աշակերտքն նորա։ Ե բ-գ 2 Եւ բացեալ զբերան իւր ուսուցանէր զնոսա, եւ ասէր։ 3 Երանի աղքատաց հոգւով, զի նոցա է արքայութիւն երկնից։ 4 Երանի սգաւորաց, զի նոքա մխիթարեսցին։ 5 Երանի հեզոց, զի նոքա ժառանգեսցեն զերկիր։ 6 Երանի որ քաղցեալ եւ ծարաւի իցեն արդարութեան, զի նոքա յագեսցին։ 7 Երանի ողորմածաց, զի նոքա ողորմութիւն գտցեն։ 8 Երանի այնոցիկ որ սուրբ են սրտիւք, զի նոքա զԱստուած',
          
'eastern bible - Աստուածը»։ Իմ աչքերը կը տեսնեն նրան։ Արդ, նա ոտքի կոխան կը դառնայ, ինչպէս ճանապարհի կաւը։ Աղիւսի 11 ծեփի օր եւ քո ջնջման օր կը փնի այն օրը. այդ օրը կը մերժի քո իրաւունքները։ Քո քաղաքները կ՚ենթարկուեն 12 ասորեստանցիների պաշարման եւ աւարին։ Քո ամուր քաղաքները կը բաժանուեն Տիւրոսից մինչեւ գետը, ծովից ծով եւ լեռից լեռ։ Եւ երկիրը ապականուի իր բնակիչներով հանդերձ՝ իր գործերի պտուղի պատճառով։ Արածացրու 13,14' , 
          
'western wiki - Լայն առումով, Հայոց Ցեղասպանութիւնը կը ներառնէ 1894-1923 թուականներուն Օսմանեան կայսրութեան եւ Թուրքիոյ տարբեր վարչակարգերուն կողմէ ծրագրուած ու հայ ժողովուրդին դէմ շարունակաբար իրականացուած ցեղասպանական քայլերը, հայրենազրկումը, հայութեան ոչնչացման ուղղուած զանգուածային կոտորածները, ցեղային զտումները, հայկական մշակութային ժառանգութեան ոչնչացումը, ինչպէս նաեւ ', 
          
'eastern wiki - Ծնվել է 1908 թվականի օգոստոսի 31-ին բանաստեղծ Արմենակ Սարոյանի և նրա կնոջ՝ Թագուհու ընտանիքում՝ գաղթած Բիթլիս քաղաքից (ներկայիս Թուրքիա), որտեղ, ըստ Սարոյանի, հայերի հետագա կյանքն անհնար էր[5]։ Մանկությունն անցկացրել է Ֆրեզնոյում (Կալիֆոռնիայի նահանգ)։ 1911 թվականին երեսունյոթամյա Արմենակ Սարոյանը մահանում է, և Վիլյամ Սարոյանը եղբոր՝ Հենրիի, և քույրերի՝ Զաբելի ու Կոզեթի հետ տեղափոխվում է որբանոց։ Երբ մայրը պետք է երեքամյա Վիլյամին թողներ որբանոցում, նա Coon Jiger անունով մի տիկնիկ է նվիրում',
          
'grabar horenatsi - Պատասխանի թղթոյ Սահակայ, եւ խոստումն կատարել զհայցուածս նորա: Մովսէս Խորենացի յաղագս մերոյս ի սկզբան յայսմ բանիցս Սահակայ Բագրատունւոյ խնդալ: Զանսպառ խաղացմունս ի քեզ աստուածայնոցն շնորհացն եւ զանդուլ հոգւոյն ի վերայ քոց իմացուածոցդ զշարժունս ծանեայ ի ձեռն գեղեցիկ խնդրոյս, յառաջ քան զմարմնոյդ՝ զհոգւոյդ ընկալեալ զծանօթութիւն, որ սիրելի իսկ իմոց ախորժակացս է, առաւել եւ ս սովորութեանցս: Վասն որոյ ոչ միայն գովել արժան է զքեզ, այլ եւ ի վերայ քո աղօթել՝ առ ի լինել քեզ միշտ այսպիսի: Զի եթէ վասն բանին մեք, որպէս ասի, պատկեր Աստուածոյ,'
          ]


with gr.Blocks() as demo:
    gr.Markdown("Check your text for compliance with the NVC rules")


    with gr.Tab("Single message analysis"):
        with gr.Row():
            text_input = gr.Textbox(lines=2, placeholder="Enter your text here")
            rec_output = gr.Label(label='Labels', num_top_classes=3)
        txt_output=gr.Textbox(label='Number of words')
        
        text_button = gr.Button("Define dialect group")
        examples_block = gr.Examples(examples=examples,
                                     inputs=[text_input], )

        text_button.click(classify, inputs=text_input,
                          outputs=[rec_output,txt_output])




demo.launch(share=True, debug=True)